In [ ]:
!wget https://hats-import.readthedocs.io/en/latest/_downloads/e5b9eb50a4fa92b9127d0f42ec502d0e/neowise_types.csv

In [ ]:
!wget https://hats-import.readthedocs.io/en/latest/_downloads/76cd21e02261120cc27526ddc583680b/neowise_schema.parquet

In [7]:
%python -m pip install git+https://github.com/astronomy-commons/hats.git@delucchi/has_contents

UsageError: Line magic function `%python` not found (But cell magic `%%python` exists, did you mean that instead?).


In [12]:
import hats

hats.__version__

'0.7.1'

In [9]:
import pandas as pd

import hats_import.pipeline as runner
from hats_import import ImportArguments, CollectionArguments, VerificationArguments
from hats_import.catalog.file_readers import CsvReader
from pathlib import Path
from dask.distributed import Client
from hats_import.pipeline import pipeline_with_client, pipeline

/astro/users/mmd11/.venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
# Load the column names and types from a side file.
type_frame = pd.read_csv("allwise_types.csv")
type_map = dict(zip(type_frame["name"], type_frame["type"]))

inputp = Path("/epyc/data3/hipscat/raw/allwise_raw")
len(list(inputp.glob("*")))

args = ImportArguments(
    output_artifact_name="allwise",
    input_file_list=list(inputp.glob("*")),
    file_reader=CsvReader(
        chunksize=250_000,
        header=None,
        sep="|",
        column_names=type_frame["name"].values.tolist(),
        type_map=type_map,
    ),
    use_schema_file="allwise_schema.parquet",
    ra_column="ra",
    dec_column="dec",
    pixel_threshold=2_000_000,
    highest_healpix_order=9,
    skymap_alt_orders=[2, 4, 6],
    row_group_kwargs={"num_rows": 250_000},

    completion_email_address="delucchi@andrew.cmu.edu",
    progress_bar=True,
    simple_progress_bar=True,    
    output_path="/epyc/data3/hats/catalogs/v06/wise/allwise_collection/",
)

In [ ]:
# with Client(local_directory="/epyc/data3/hats/tmp/", n_workers=10, threads_per_worker=1) as client:
#     pipeline_with_client(args, client)

In [ ]:
args = (
    CollectionArguments(
        output_artifact_name="allwise_collection",
        output_path="/epyc/data3/hats/catalogs/v06/wise",
        completion_email_address="delucchi@andrew.cmu.edu",
        progress_bar=True,
        simple_progress_bar=True,
    )
    .catalog(
        output_artifact_name="allwise",
    )
    .add_margin(margin_threshold=5.0, is_default=True)
)

with Client(local_directory="/epyc/data3/hats/tmp/", n_workers=10, threads_per_worker=1) as client:
    pipeline_with_client(args, client)

In [ ]:
args = VerificationArguments(
    input_catalog_path="/epyc/data3/hats/catalogs/v06/wise/allwise_collection/allwise",
    output_path="./verification/allwise",
)

pipeline(args)

In [10]:
# Load the column names and types from a side file.
type_frame = pd.read_csv("neowise_types.csv")
type_map = dict(zip(type_frame["name"], type_frame["type"]))

inputp = Path("/epyc/data3/NEOWISE-yr8/irsa.ipac.caltech.edu/data/download/neowiser_year8")

args = ImportArguments(
    output_artifact_name="neowise",
    input_file_list=list(inputp.glob("*.bz2")),
    file_reader=CsvReader(
        chunksize=250_000,
        header=None,
        sep="|",
        column_names=type_frame["name"].values.tolist(),
        type_map=type_map,
        compression="bz2",
    ),
    use_schema_file="neowise_schema.parquet",
    ra_column="RA",
    dec_column="DEC",
    # sort_columns="QUICK_OBJECT_ID",
    highest_healpix_order=9,
    skymap_alt_orders=[2, 4, 6],
    row_group_kwargs={"num_rows": 500_000},

    completion_email_address="delucchi@andrew.cmu.edu",
    progress_bar=True,
    simple_progress_bar=True,    
    output_path="/epyc/data3/hats/catalogs/v06/wise/neowise_collection/",
    # resume=False,
)

In [11]:
with Client(local_directory="/epyc/data3/hats/tmp/", n_workers=10, threads_per_worker=1) as client:
    pipeline_with_client(args, client)

Planning  : 100%|██████████| 4/4 [19:29<00:00, 292.39s/it] 


tmp_path (/epyc/data3/hats/catalogs/v06/wise/neowise_collection/neowise/intermediate) contains intermediate files; resuming prior progress.


Reducing  :   1%|          | 175/24534 [04:18<12:52:41,  1.90s/it]2025-11-20 13:27:06,842 - distributed.scheduler - WARNING - Removing worker 'tcp://127.0.0.1:43057' caused the cluster to lose already computed task(s), which will be recomputed elsewhere: {'reduce_pixel_shards-69ca5dc302c5a05290fd88f00c827397', 'reduce_pixel_shards-022037f5fba4227013e4a3d93f7c2bc5', 'reduce_pixel_shards-42a03e871d46aeec3f477311575630b0', 'reduce_pixel_shards-c2f29601c3774c25997048d81f9f452c', 'reduce_pixel_shards-98e274aa8bc2e84cb9d8da0805c74627', 'reduce_pixel_shards-d1ea6d9a69920b5c0ec267a171f503d3', 'reduce_pixel_shards-633757901be39a9d55254cbf20c6fdcc', 'reduce_pixel_shards-2b2d57aaf79447ca560fa740ebe8e1a6', 'reduce_pixel_shards-4fed0a6b5ba760d9bc4506a37eb2fbea', 'reduce_pixel_shards-c4f6dec1d03f1fe149a559797003d040', 'reduce_pixel_shards-93f8bc1cb041c98c8ab01cbca40ccb8a', 'reduce_pixel_shards-7786468720130f4378f5cd092e113847', 'reduce_pixel_shards-58468d851b45568f3cc17dcc9048f694', 'reduce_pixel_sh

In [13]:
args = (
    CollectionArguments(
        output_artifact_name="neowise_collection",
        output_path="/epyc/data3/hats/catalogs/v06/wise",
        completion_email_address="delucchi@andrew.cmu.edu",
        progress_bar=True,
        simple_progress_bar=True,
    )
    .catalog(
        output_artifact_name="neowise",
    )
    .add_margin(margin_threshold=5.0, is_default=True)
)

with Client(local_directory="/epyc/data3/hats/tmp/", n_workers=10, threads_per_worker=1) as client:
    pipeline_with_client(args, client)

Finishing : 100%|██████████| 2/2 [00:16<00:00,  8.39s/it]


In [14]:
args = VerificationArguments(
    input_catalog_path="/epyc/data3/hats/catalogs/v06/wise/neowise_collection/neowise",
    output_path="./verification/neowise",
)

pipeline(args)

Loading dataset and schema.

Starting: Test hats.io.validation.is_valid_catalog.
Validating catalog at path /epyc/data3/hats/catalogs/v06/wise/neowise_collection/neowise ... 
Found 39774 partitions.
Approximate coverage is 100.00 % of the sky.
Result: PASSED

Starting: Test that files in _metadata match the data files on disk.
Result: PASSED

Starting: Test that number of rows are equal.
	file footers vs catalog properties
	file footers vs _metadata
Result: PASSED

Starting: Test that schemas are equal, excluding metadata.
	_common_metadata vs truth
	_metadata vs truth
	file footers vs truth
Result: PASSED

Verifier results written to verification/neowise/verifier_results.csv
Elapsed time (seconds): 666.07
